* [Issue 2](https://github.com/salgo60/Dogpark_Sweden/issues/2)
* denna notebook [Dogpark_Sweden.ipynb](https://github.com/salgo60/Dogpark_Sweden/blob/main/notebook/Dogpark_Sweden.ipynb)

In [ ]:
import requests, json, time
from bs4 import BeautifulSoup

BASE_URL = "https://www.hundlistan.se/"
params = {
    "mylisting-ajax": "1",
    "action": "get_listings",
    "security": "5e528da4d5",  # säkerhets-token (kan behöva uppdateras om Hundlistan ändrar den)
    "form_data[preserve_page]": "true",
    "form_data[sort]": "latest",
    "form_data[region]": "",
    "form_data[search_location]": "",
    "form_data[lat]": "false",
    "form_data[lng]": "false",
    "listing_type": "hundpark",
    "listing_wrap": "col-md-12 grid-item"
}

features = []

for page in range(1, 40):  # 1 till 39
    params["form_data[page]"] = str(page)
    print(f"Hämtar sida {page}/39 ...", end="\r")

    r = requests.get(BASE_URL, params=params)
    if r.status_code != 200:
        print(f"\n⚠️ Sida {page} misslyckades ({r.status_code})")
        continue

    data = r.json()
    html = data.get("html", "")
    soup = BeautifulSoup(html, "html.parser")

    for item in soup.select(".lf-item-container"):
        try:
            data_id = item.get("data-id")
            title = item.select_one(".listing-preview-title").get_text(strip=True)
            href = item.select_one("a")["href"]
            lan = item.select_one(".lf-contact li").get_text(strip=True)
            loc = json.loads(item.get("data-locations"))[0]

            address = loc.get("address")
            lat = float(loc.get("lat"))
            lng = float(loc.get("lng"))

            popup_html = f"""
            <b>{title}</b><br>
            {address}<br>
            {lan}<br>
            <a href="{href}" target="_blank">Visa på Hundlistan</a>
            """.strip()

            features.append({
                "type": "Feature",
                "geometry": {"type": "Point", "coordinates": [lng, lat]},
                "properties": {
                    "id": data_id,
                    "namn": title,
                    "adress": address,
                    "lan": lan,
                    "url": href,
                    "popup": popup_html
                }
            })
        except Exception as e:
            print(f"\n⚠️ Fel vid parsing: {e}")

    time.sleep(0.5)  # vänlig delay mot servern

geojson = {
    "type": "FeatureCollection",
    "features": features
}

with open("hundparker_umap.geojson", "w", encoding="utf-8") as f:
    json.dump(geojson, f, ensure_ascii=False, indent=2)

print(f"\n✅ Klart! {len(features)} hundparker sparade i hundparker_umap.geojson")


### Skapa karta


In [1]:
import folium
import json

# Läs in GeoJSON-filen
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

# Skapa grundkartan (centrerad på Sverige)
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# Gå igenom varje hundpark och skapa en marker
for feature in data["features"]:
    props = feature["properties"]
    coords = feature["geometry"]["coordinates"]
    lon, lat = coords[0], coords[1]

    # Popup med tydlig formatering
    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress', 'Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan', 'Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(m)

# Lägg till lagerkontroll
folium.LayerControl().add_to(m)

# Spara kartan
#m.save("hundparker_folium_snygg.html")
print("✅ Snygg Folium-karta sparad som hundparker_folium_snygg.html")


✅ Snygg Folium-karta sparad som hundparker_folium_snygg.html


In [2]:
m

In [3]:
import folium
import json

# Läs in GeoJSON
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

# Skapa kartan
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# Lägg till infobox med logga och GitHub-länk
info_html = """
<div style="
    position: fixed; 
    top: 10px; left: 10px; 
    z-index: 9999; 
    background-color: rgba(255,255,255,0.9); 
    padding: 10px; 
    border-radius: 12px; 
    box-shadow: 0 0 10px rgba(0,0,0,0.2);
    font-family: Arial; font-size: 13px;">
  <div style="text-align:center;">
    <img src="https://raw.githubusercontent.com/salgo60/Dogpark_Sweden/main/dogparksweden.png" 
         alt="Dogpark Sweden" width="180"><br>
    <a href="https://github.com/salgo60/Dogpark_Sweden" target="_blank" 
       style="color:#0077cc; text-decoration:none; font-weight:bold;">
       🐾 Dogpark Sweden på GitHub
    </a>
  </div>
</div>
"""
m.get_root().html.add_child(folium.Element(info_html))

# Lägg till markörer
for f in data["features"]:
    p = f["properties"]
    lon, lat = f["geometry"]["coordinates"]
    popup_html = f"""
    <div style="font-family:Arial; font-size:13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {p['namn']}</b><br>
      📍 {p.get('adress','Okänd adress')}<br>
      🏙️ {p.get('lan','Okänt län')}<br>
      <a href="{p['url']}" target="_blank" style="color:#0077cc;">🔗 Visa på Hundlistan</a>
    </div>
    """
    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=p["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(m)

m.save("hundparker_folium_dogparksweden_2.html")
print("✅ Karta skapad: hundparker_folium_dogparksweden_2.html")


✅ Karta skapad: hundparker_folium_dogparksweden_2.html


In [4]:
m


In [5]:
import folium
import json

# Läs in GeoJSON-filen
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

# Skapa grundkartan (centrerad på Sverige)
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# 💡 Lägg till infobox med logga och GitHub-länk
info_html = """
<div style="
    position: fixed;
    top: 10px; left: 10px;
    z-index: 9999;
    background-color: rgba(255,255,255,0.95);
    padding: 10px 12px;
    border-radius: 12px;
    box-shadow: 0 0 10px rgba(0,0,0,0.3);
    font-family: Arial, sans-serif;
    font-size: 13px;
    max-width: 230px;
">
  <div style="text-align:center;">
    <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
         alt="Dogpark Sweden" width="200" style="border-radius:8px; margin-bottom:5px;"><br>
    <a href="https://github.com/salgo60/Dogpark_Sweden"
       target="_blank"
       style="color:#0077cc; font-weight:bold; text-decoration:none;">
       🐾 GITHUB where the magic happens
    </a>
  </div>
</div>
"""
m.get_root().html.add_child(folium.Element(info_html))

# Lägg till alla hundparker som markörer
for feature in data["features"]:
    props = feature["properties"]
    coords = feature["geometry"]["coordinates"]
    lon, lat = coords[0], coords[1]

    # Popup med tydlig formatering
    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress', 'Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan', 'Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(m)

# Lägg till lagerkontroll
folium.LayerControl().add_to(m)

# Spara kartan
m.save("hundparker_folium_snygg.html")
print("✅ Folium-karta klar: hundparker_folium_snygg.html")


✅ Folium-karta klar: hundparker_folium_snygg.html


In [6]:
m


### version 3  
Har collapseble infobox

In [7]:
import folium
import json

# Läs in GeoJSON-filen
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

# Skapa grundkartan (centrerad på Sverige)
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# 💡 Lägg till infobox med logga och GitHub-länk
info_html = """
<style>
#infoBox {
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 240px;
  transition: all 0.3s ease-in-out;
}

#toggleBtn {
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}

#toggleBtn:hover {
  background-color: #005fa3;
}

#infoContent {
  display: block; /* 👈 visa innehållet direkt */
  margin-top: 8px;
}

@media (max-width: 600px) {
  #infoBox {
    max-width: 180px;
    font-size: 12px;
  }
}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>
  </div>
</div>

<script>
  const btn = document.getElementById('toggleBtn');
  const content = document.getElementById('infoContent');
  let open = true; // 👈 startläge: öppen
  btn.onclick = () => {
    open = !open;
    content.style.display = open ? 'block' : 'none';
    btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
  };
</script>
"""


m.get_root().html.add_child(folium.Element(info_html))

# Lägg till alla hundparker som markörer
for feature in data["features"]:
    props = feature["properties"]
    coords = feature["geometry"]["coordinates"]
    lon, lat = coords[0], coords[1]

    # Popup med tydlig formatering
    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress', 'Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan', 'Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(m)

# Lägg till lagerkontroll
folium.LayerControl().add_to(m)

# Spara kartan
m.save("hundparker_folium_snygg.html")
m.save("hundparker_folium_snygg3.html")
print("✅ Folium-karta klar: hundparker_folium_snygg.html")


✅ Folium-karta klar: hundparker_folium_snygg.html


In [8]:
m


## version 4 hämta fråm OSM 

In [9]:
import requests

# 🗺️ Overpass API-endpoint
overpass_url = "https://overpass-api.de/api/interpreter"

# Bounding box för Sverige ungefär: (syd, väst, nord, öst)
sweden_bbox = "55.0,10.5,69.2,24.2"

# Overpass-fråga: alla noder, vägar och relationer med leisure=dog_park i Sverige
overpass_query = f"""
[out:json][timeout:60];
nwr["leisure"="dog_park"]({sweden_bbox});
out center;
"""

print("⏳ Hämtar hundrastgårdar från OSM...")
response = requests.get(overpass_url, params={"data": overpass_query})
osm_data = response.json()
print(f"✅ Hittade {len(osm_data['elements'])} objekt från OSM")

# Skapa ett separat lager för OSM-datan
osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue

    name = el["tags"].get("name", "Okänd rastgård")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐕 {name}</b><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {el['id']}<br>
          <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a>
        </p>
      </details>
    </div>
    """

    folium.CircleMarker(
        location=[lat, lon],
        radius=4,
        color="purple",
        fill=True,
        fill_opacity=0.6,
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
    ).add_to(osm_layer)

# Lägg till OSM-lagret till kartan
osm_layer.add_to(m)


⏳ Hämtar hundrastgårdar från OSM...
✅ Hittade 923 objekt från OSM


In [ ]:
folium.LayerControl(collapsed=False).add_to(m)

In [ ]:
m

In [ ]:
import folium
import json
import requests
import os

# --------------------------------------------------
# 🗺️ 1. Skapa grundkartan
# --------------------------------------------------
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# --------------------------------------------------
# 🐾 2. Infobox (öppen från start, collapsible)
# --------------------------------------------------
info_html = """
<style>
#infoBox {
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 260px;
  transition: all 0.3s ease-in-out;
}
#toggleBtn {
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}
#toggleBtn:hover { background-color: #005fa3; }
#infoContent { display: block; margin-top: 8px; }
.version-list {
  text-align: left;
  margin-top: 10px;
  padding-left: 12px;
}
.version-list a {
  color: #0077cc;
  text-decoration: none;
}
.version-list a:hover {
  text-decoration: underline;
}
.version-list li {
  margin-bottom: 4px;
}
@media (max-width: 600px) {
  #infoBox { max-width: 190px; font-size: 12px; }
}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <b style="display:block; text-align:center;">📌 Versioner</b>
    <ol class="version-list">
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OpenStreetMap-lager</a></li>
    </ol>
  </div>
</div>

<script>
  const btn = document.getElementById('toggleBtn');
  const content = document.getElementById('infoContent');
  let open = true;
  btn.onclick = () => {
    open = !open;
    content.style.display = open ? 'block' : 'none';
    btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
  };
</script>
"""
m.get_root().html.add_child(folium.Element(info_html))

# --------------------------------------------------
# 🦴 3. Hundlistan-data (lager 1)
# --------------------------------------------------
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

hundlistan_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")

for feature in data["features"]:
    props = feature["properties"]
    lon, lat = feature["geometry"]["coordinates"]

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress','Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan','Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>
    """
    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hundlistan_layer)

hundlistan_layer.add_to(m)

# --------------------------------------------------
# 🐕‍🦺 4. OSM Hundrastgårdar (lager 2)
# --------------------------------------------------
osm_file = "osm_dogparks_sweden.json"

if os.path.exists(osm_file):
    print("📂 Läser OSM-data lokalt...")
    with open(osm_file, "r", encoding="utf-8") as f:
        osm_data = json.load(f)
else:
    print("⏳ Hämtar hundrastgårdar från OSM...")
    overpass_url = "https://overpass-api.de/api/interpreter"
    sweden_bbox = "55.0,10.5,69.2,24.2"
    query = f"""
    [out:json][timeout:60];
    nwr["leisure"="dog_park"]({sweden_bbox});
    out center;
    """
    r = requests.get(overpass_url, params={"data": query})
    osm_data = r.json()
    with open(osm_file, "w", encoding="utf-8") as f:
        json.dump(osm_data, f, ensure_ascii=False, indent=2)
    print(f"✅ Sparade {len(osm_data['elements'])} objekt till {osm_file}")

osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue

    name = el["tags"].get("name", "Okänd rastgård")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:purple;">🐕 {name}</b><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {el['id']}<br>
          <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a>
        </p>
      </details>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)

osm_layer.add_to(m)

# --------------------------------------------------
# 🎛️ 5. Layer-kontroll + spara
# --------------------------------------------------
folium.LayerControl(collapsed=False).add_to(m)
m.save("hundparker_folium_snygg.html")
m.save("hundparker_folium_snygg_3.html")
print("✅ Klar: hundparker_folium_snygg_3.html (Hundlistan + OSM-lager)")


m

In [ ]:
m

In [ ]:
import folium
from folium.plugins import MiniMap, LocateControl
import json
import requests
import os
from datetime import datetime

# --------------------------------------------------
# 🗓️ Datum för infobox
# --------------------------------------------------
today = datetime.now().strftime("%-d %b %Y")  # ex. "6 okt 2025"

# --------------------------------------------------
# 🗺️ 1. Skapa grundkartan med flera bakgrundsalternativ
# --------------------------------------------------
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles=None)

basemaps = {
    "CartoDB Positron": "CartoDB positron",
    "OpenStreetMap": "OpenStreetMap",
    "Stamen Terrain": "Stamen Terrain",
    "Stamen Toner": "Stamen Toner",
    "Esri WorldImagery": "https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}"
}
for name, tiles in basemaps.items():
    folium.TileLayer(tiles, name=name, attr=name).add_to(m)

# --------------------------------------------------
# 🧭 2. Lägg till MiniMap och "Min plats"-knapp
# --------------------------------------------------
MiniMap(toggle_display=True).add_to(m)
LocateControl(auto_start=False, position="topleft").add_to(m)

# --------------------------------------------------
# 🐾 3. Infobox (öppen från start, collapsible, med versioner + datum)
# --------------------------------------------------
info_html = f"""
<style>
#infoBox {{
  position: fixed; top: 10px; left: 10px; z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px; border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif; font-size: 13px;
  max-width: 260px; transition: all 0.3s ease-in-out;
}}
#toggleBtn {{
  background-color: #0077cc; color: white; border: none;
  border-radius: 8px; padding: 6px 10px; cursor: pointer;
  font-size: 13px; width: 100%; text-align: center;
}}
#toggleBtn:hover {{ background-color: #005fa3; }}
#infoContent {{ display: block; margin-top: 8px; }}
.version-list {{ text-align: left; margin-top: 10px; padding-left: 12px; }}
.version-list a {{ color: #0077cc; text-decoration: none; }}
.version-list a:hover {{ text-decoration: underline; }}
.version-list li {{ margin-bottom: 4px; }}
@media (max-width: 600px) {{
  #infoBox {{ max-width: 190px; font-size: 12px; }}
}}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <b style="display:block; text-align:center;">📌 Versioner</b>
    <ol class="version-list">
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OSM-lager</a></li>
      <li><b>🆕 Version 4:</b> Minimap + Min plats + Bakgrundskartor</li>
    </ol>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <p style="text-align:center; color:#555; font-size:12px;">
      📅 Senast uppdaterad: <b>{today}</b>
    </p>
  </div>
</div>

<script>
  const btn=document.getElementById('toggleBtn');
  const content=document.getElementById('infoContent');
  let open=true;
  btn.onclick=()=>{{open=!open;
    content.style.display=open?'block':'none';
    btn.innerText=open?'❌ Dölj info':'📖 Visa info';
  }};
</script>
"""
m.get_root().html.add_child(folium.Element(info_html))

# --------------------------------------------------
# 🦴 4. Hundlistan-data (lager 1)
# --------------------------------------------------
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

hundlistan_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")

for feature in data["features"]:
    props = feature["properties"]
    lon, lat = feature["geometry"]["coordinates"]

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress','Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan','Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>
    """
    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hundlistan_layer)

hundlistan_layer.add_to(m)

# --------------------------------------------------
# 🐕‍🦺 5. OSM Hundrastgårdar (lager 2, sparas lokalt)
# --------------------------------------------------
osm_file = "osm_dogparks_sweden.json"

if os.path.exists(osm_file):
    print("📂 Läser OSM-data lokalt...")
    with open(osm_file, "r", encoding="utf-8") as f:
        osm_data = json.load(f)
else:
    print("⏳ Hämtar hundrastgårdar från OSM...")
    overpass_url = "https://overpass-api.de/api/interpreter"
    sweden_bbox = "55.0,10.5,69.2,24.2"
    query = f"""
    [out:json][timeout:60];
    nwr["leisure"="dog_park"]({sweden_bbox});
    out center;
    """
    r = requests.get(overpass_url, params={"data": query})
    osm_data = r.json()
    with open(osm_file, "w", encoding="utf-8") as f:
        json.dump(osm_data, f, ensure_ascii=False, indent=2)
    print(f"✅ Sparade {len(osm_data['elements'])} objekt till {osm_file}")

osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue

    name = el["tags"].get("name", "Okänd rastgård")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:purple;">🐕 {name}</b><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {el['id']}<br>
          <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a>
        </p>
      </details>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)

osm_layer.add_to(m)

# --------------------------------------------------
# 🎛️ 6. Layer-kontroll + spara
# --------------------------------------------------
folium.LayerControl(collapsed=False).add_to(m)
m.save("hundparker_folium_v4.html")
print("✅ Klar: hundparker_folium_v4.html (v4 – Minimap, Min plats, Bakgrundskartor, Datum)")


m


In [ ]:
m

# Version 5
<br>✨ Nyheter i Version 5
<br>Funktion	Beskrivning
<br>🧭 MiniMap + Min plats	Översiktskarta och GPS-knapp
<br>🗺️ Basemap-växling	Välj bakgrund (OSM, Carto, Stamen, Esri)
<br>🎚️ Kollapsbar LayerControl	Tar mindre plats på mobil
<br>🎨 Kollapsbar Legend	Förklaring av lager och ikoner
<br>📅 Datumstämpel	“Senast uppdaterad” visas i infoboxen

In [ ]:
import folium
from folium.plugins import MiniMap, LocateControl
import json, requests, os
from datetime import datetime
from folium import Html

# --------------------------------------------------
# 🗓️ Svenskt datum + tid
# --------------------------------------------------
months = [
    "januari", "februari", "mars", "april", "maj", "juni",
    "juli", "augusti", "september", "oktober", "november", "december"
]
now = datetime.now()
today = f"{now.day} {months[now.month - 1]} {now.year} {now.strftime('%H:%M')}"

# --------------------------------------------------
# 🗺️ Grundkarta – bättre centrerad över Sverige
# --------------------------------------------------
m = folium.Map(location=[60.5, 17.5], zoom_start=5.5, tiles=None)

basemaps = {
    "CartoDB Positron": "CartoDB positron",
    "OpenStreetMap": "OpenStreetMap",
    "Stamen Terrain": "Stamen Terrain",
    "Stamen Toner": "Stamen Toner",
    "Esri WorldImagery": "https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}"
}
for name, tiles in basemaps.items():
    folium.TileLayer(tiles, name=name, attr=name).add_to(m)

# --------------------------------------------------
# 🧭 MiniMap + "Min plats"
# --------------------------------------------------
MiniMap(toggle_display=True).add_to(m)
LocateControl(auto_start=False, position="topleft").add_to(m)

# --------------------------------------------------
# 🐾 Infobox med skapad-datum
# --------------------------------------------------
info_html = f"""
<style>
#infoBox {{
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 260px;
  transition: all 0.3s ease-in-out;
}}
#toggleBtn {{
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}}
#toggleBtn:hover {{ background-color: #005fa3; }}
#infoContent {{ display: block; margin-top: 8px; }}
.version-list {{
  text-align: left;
  margin-top: 10px;
  padding-left: 24px;
  list-style-type: decimal;
}}
.version-list a {{ color: #0077cc; text-decoration: none; }}
.version-list a:hover {{ text-decoration: underline; }}
.version-list li {{ margin-bottom: 4px; line-height: 1.4; }}
@media (max-width: 600px) {{
  #infoBox {{ max-width: 190px; font-size: 12px; }}
}}
</style>

<div id="infoBox">
 <button id="toggleBtn">❌ Dölj info</button>
 <div id="infoContent">
  <div style="text-align:center;">
   <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
        alt="Dogpark Sweden" width="180" style="border-radius:8px;margin-bottom:5px;"><br>
   <a href="https://github.com/salgo60/Dogpark_Sweden" target="_blank"
      style="color:#0077cc;font-weight:bold;text-decoration:none;">
      🐾 GITHUB where the magic happens
   </a>
  </div>

  <hr style="margin:10px 0;border:none;border-top:1px solid #ccc;">
  <b style="display:block;text-align:center;">📌 Versioner</b>
  <ol class="version-list">
    <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
    <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
    <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OSM-lager</a></li>
    <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_v4.html" target="_blank">Hundlistan + OSM (v4)</a></li>
    <li><b>🆕 Version 6:</b> Bättre centrering + datum med tid</li>
  </ol>

  <hr style="margin:10px 0;border:none;border-top:1px solid #ccc;">
  <p style="text-align:center;color:#555;font-size:12px;">
    <span style="font-size:14px;">📅</span> Skapad: <b>{today}</b>
  </p>
 </div>
</div>

<script>
 const btn = document.getElementById('toggleBtn');
 const content = document.getElementById('infoContent');
 let open = true;
 btn.onclick = () => {{
   open = !open;
   content.style.display = open ? 'block' : 'none';
   btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
 }};
</script>
"""
m.get_root().html.add_child(Html(info_html, script=True))

# --------------------------------------------------
# 🦴 Hundlistan-lager
# --------------------------------------------------
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

hundlistan_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")
for feature in data["features"]:
    props = feature["properties"]
    lon, lat = feature["geometry"]["coordinates"]
    popup_html = f"""
    <div style="font-family:Arial;font-size:13px;">
      <b style="font-size:14px;color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress','Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan','Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc;text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>"""
    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hundlistan_layer)
hundlistan_layer.add_to(m)

# --------------------------------------------------
# 🐕‍🦺 OSM-lager
# --------------------------------------------------
osm_file = "osm_dogparks_sweden.json"
if os.path.exists(osm_file):
    with open(osm_file, "r", encoding="utf-8") as f:
        osm_data = json.load(f)
else:
    print("⏳ Hämtar hundrastgårdar från OSM…")
    query = """[out:json][timeout:60];
      nwr["leisure"="dog_park"](55.0,10.5,69.2,24.2);
      out center;"""
    r = requests.get("https://overpass-api.de/api/interpreter", params={"data": query})
    osm_data = r.json()
    with open(osm_file, "w", encoding="utf-8") as f:
        json.dump(osm_data, f, ensure_ascii=False, indent=2)

osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")
for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue
    name = el["tags"].get("name", "Okänd rastgård")
    popup_html = f"""
    <div style="font-family:Arial;font-size:13px;">
      <b style="font-size:14px;color:purple;">🐕 {name}</b><br>
      <details><summary style="color:#0077cc;cursor:pointer;">📋 Visa mer info</summary>
      <p><b>OSM-ID:</b> {el['id']}<br>
      <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}"
         target="_blank" style="color:#0077cc;">
         🔗 Öppna i OSM</a></p></details></div>"""
    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)
osm_layer.add_to(m)

# --------------------------------------------------
# 🎛️ LayerControl + spara
# --------------------------------------------------
folium.LayerControl(collapsed=True, position="topright").add_to(m)
m.save("hundparker_folium_v6_2.html")
print("✅ Klar: hundparker_folium_v6_2.html (centrerad + skapad-tid)")


In [ ]:
m


### Ny version med GPS länk OSM 3_2

In [ ]:
import folium
import json
import requests
import os

# --------------------------------------------------
# 🗺️ 1. Skapa grundkartan
# --------------------------------------------------
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# --------------------------------------------------
# 🐾 2. Infobox (öppen från start, collapsible)
# --------------------------------------------------
info_html = """
<style>
#infoBox {
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 260px;
  transition: all 0.3s ease-in-out;
}
#toggleBtn {
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}
#toggleBtn:hover { background-color: #005fa3; }
#infoContent { display: block; margin-top: 8px; }
.version-list {
  text-align: left;
  margin-top: 10px;
  padding-left: 12px;
}
.version-list a {
  color: #0077cc;
  text-decoration: none;
}
.version-list a:hover {
  text-decoration: underline;
}
.version-list li {
  margin-bottom: 4px;
}
@media (max-width: 600px) {
  #infoBox { max-width: 190px; font-size: 12px; }
}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <b style="display:block; text-align:center;">📌 Versioner</b>
    <ol class="version-list">
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OpenStreetMap-lager</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_2.html" target="_blank">🌍 Hundlistan + OSM-version</a></li>
    </ol>

    <div style="text-align:center; margin-top:8px;">
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank"
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a>
    </div>
  </div>
</div>

<script>
  const btn = document.getElementById('toggleBtn');
  const content = document.getElementById('infoContent');
  let open = true;
  btn.onclick = () => {
    open = !open;
    content.style.display = open ? 'block' : 'none';
    btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
  };
</script>
"""

m.get_root().html.add_child(folium.Element(info_html))

# --------------------------------------------------
# 🦴 3. Hundlistan-data (lager 1)
# --------------------------------------------------
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

hundlistan_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")

for feature in data["features"]:
    props = feature["properties"]
    lon, lat = feature["geometry"]["coordinates"]

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress','Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan','Okänt län')}</span><br>
      <span style="color:#777;">🧭 
        <span id='coord_{lat:.5f}_{lon:.5f}'>{lat:.5f}, {lon:.5f}</span>
        <button onclick="navigator.clipboard.writeText('{lat:.5f}, {lon:.5f}'); 
                         this.innerText='✅'; 
                         setTimeout(()=>this.innerText='📋',1000);"
                style="background:none; border:none; cursor:pointer; color:#0077cc; font-size:13px;"
                title="Kopiera koordinat">📋</button>
      </span><br><br>
    
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a><br>
      <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
         target="_blank" style="color:#d97706; text-decoration:none;">
         🗺️ Skapa OSM Note här
      </a><br>
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank" 
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a>
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hundlistan_layer)

hundlistan_layer.add_to(m)

# --------------------------------------------------
# 🐕‍🦺 4. OSM Hundrastgårdar (lager 2)
# --------------------------------------------------
osm_file = "osm_dogparks_sweden.json"

if os.path.exists(osm_file):
    print("📂 Läser OSM-data lokalt...")
    with open(osm_file, "r", encoding="utf-8") as f:
        osm_data = json.load(f)
else:
    print("⏳ Hämtar hundrastgårdar från OSM...")
    overpass_url = "https://overpass-api.de/api/interpreter"
    sweden_bbox = "55.0,10.5,69.2,24.2"
    query = f"""
    [out:json][timeout:60];
    nwr["leisure"="dog_park"]({sweden_bbox});
    out center;
    """
    r = requests.get(overpass_url, params={"data": query})
    osm_data = r.json()
    with open(osm_file, "w", encoding="utf-8") as f:
        json.dump(osm_data, f, ensure_ascii=False, indent=2)
    print(f"✅ Sparade {len(osm_data['elements'])} objekt till {osm_file}")

osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue

    name = el["tags"].get("name", "Okänd rastgård")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:purple;">🐕 {name}</b><br>
      <span style="color:#777;">🧭 <span id='coord_{lat:.5f}_{lon:.5f}'>{lat:.5f}, {lon:.5f}</span>
        <button onclick="navigator.clipboard.writeText('{lat:.5f}, {lon:.5f}'); 
                         this.innerText='✅'; 
                         setTimeout(()=>this.innerText='📋',1000);"
                style="background:none; border:none; cursor:pointer; color:#0077cc; font-size:13px;"
                title="Kopiera koordinat">📋</button>
      </span><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {el['id']}<br>
          <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a><br>
          <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
             target="_blank" style="color:#d97706;">🗺️ Skapa OSM Note här</a>
        </p>
      </details>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)

osm_layer.add_to(m)

# --------------------------------------------------
# 🎛️ 5. Layer-kontroll + spara
# --------------------------------------------------
folium.LayerControl(collapsed=False).add_to(m)
m.save("hundparker_folium_snygg.html")
m.save("hundparker_folium_snygg_3_2.html")
print("✅ Klar: hundparker_folium_snygg_3_2.html (Hundlistan + OSM-lager)")


In [ ]:
m


In [ ]:
import folium
import json
import requests
import os

# --------------------------------------------------
# 🗺️ 1. Skapa grundkartan
# --------------------------------------------------
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# --------------------------------------------------
# 🐾 2. Infobox (öppen från start, collapsible)
# --------------------------------------------------
info_html = """
<style>
#infoBox {
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 260px;
  transition: all 0.3s ease-in-out;
}
#toggleBtn {
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}
#toggleBtn:hover { background-color: #005fa3; }
#infoContent { display: block; margin-top: 8px; }
.version-list {
  text-align: left;
  margin-top: 10px;
  padding-left: 12px;
}
.version-list a {
  color: #0077cc;
  text-decoration: none;
}
.version-list a:hover {
  text-decoration: underline;
}
.version-list li {
  margin-bottom: 4px;
}
@media (max-width: 600px) {
  #infoBox { max-width: 190px; font-size: 12px; }
}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <b style="display:block; text-align:center;">📌 Versioner</b>
    <ol class="version-list">
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OpenStreetMap-lager</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_2.html" target="_blank">🌍 Hundlistan + OSM-version</a></li>
    </ol>

    <div style="text-align:center; margin-top:8px;">
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank"
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a>
    </div>
  </div>
</div>

<script>
  const btn = document.getElementById('toggleBtn');
  const content = document.getElementById('infoContent');
  let open = true;
  btn.onclick = () => {
    open = !open;
    content.style.display = open ? 'block' : 'none';
    btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
  };
</script>
"""

m.get_root().html.add_child(folium.Element(info_html))

# --------------------------------------------------
# 🦴 3. Hundlistan-data (lager 1)
# --------------------------------------------------
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

hundlistan_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")

for feature in data["features"]:
    props = feature["properties"]
    lon, lat = feature["geometry"]["coordinates"]

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress','Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan','Okänt län')}</span><br>
      <span style="color:#777;">🧭 
        <span id='coord_{lat:.5f}_{lon:.5f}'>{lat:.5f}, {lon:.5f}</span>
        <button onclick="navigator.clipboard.writeText('{lat:.5f}, {lon:.5f}'); 
                         this.innerText='✅'; 
                         setTimeout(()=>this.innerText='📋',1000);"
                style="background:none; border:none; cursor:pointer; color:#0077cc; font-size:13px;"
                title="Kopiera koordinat">📋</button>
      </span><br><br>
    
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a><br>
      <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
         target="_blank" style="color:#d97706; text-decoration:none;">
         🗺️ Skapa OSM Note här
      </a><br>
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank" 
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a>
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hundlistan_layer)

hundlistan_layer.add_to(m)

# --------------------------------------------------
# 🐕‍🦺 4. OSM Hundrastgårdar (lager 2)
# --------------------------------------------------
osm_file = "osm_dogparks_sweden.json"

if os.path.exists(osm_file):
    print("📂 Läser OSM-data lokalt...")
    with open(osm_file, "r", encoding="utf-8") as f:
        osm_data = json.load(f)
else:
    print("⏳ Hämtar hundrastgårdar från OSM...")
    overpass_url = "https://overpass-api.de/api/interpreter"
    sweden_bbox = "55.0,10.5,69.2,24.2"
    query = f"""
    [out:json][timeout:60];
    nwr["leisure"="dog_park"]({sweden_bbox});
    out center;
    """
    r = requests.get(overpass_url, params={"data": query})
    osm_data = r.json()
    with open(osm_file, "w", encoding="utf-8") as f:
        json.dump(osm_data, f, ensure_ascii=False, indent=2)
    print(f"✅ Sparade {len(osm_data['elements'])} objekt till {osm_file}")

osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue

    name = el["tags"].get("name", "Okänd rastgård")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:purple;">🐕 {name}</b><br>
      <span style="color:#777;">🧭 <span id='coord_{lat:.5f}_{lon:.5f}'>{lat:.5f}, {lon:.5f}</span>
        <button onclick="navigator.clipboard.writeText('{lat:.5f}, {lon:.5f}'); 
                         this.innerText='✅'; 
                         setTimeout(()=>this.innerText='📋',1000);"
                style="background:none; border:none; cursor:pointer; color:#0077cc; font-size:13px;"
                title="Kopiera koordinat">📋</button>
      </span><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {el['id']}<br>
          <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a><br>
          <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
             target="_blank" style="color:#d97706;">🗺️ Skapa OSM Note här</a>
        </p>
      </details>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)

osm_layer.add_to(m)
# --------------------------------------------------
# 📍 6. "Min plats"-knapp (geolocation)
# --------------------------------------------------
geolocate_js = """
<script>
function addLocateButton(map){
  const btn = L.control({position: 'topleft'});
  btn.onAdd = function(){
    const div = L.DomUtil.create('div', 'leaflet-bar leaflet-control leaflet-control-custom');
    div.innerHTML = '📍<br><small style="font-size:10px;">Min plats</small>';
    div.style.backgroundColor = 'white';
    div.style.cursor = 'pointer';
    div.style.textAlign = 'center';
    div.style.padding = '4px';
    div.title = 'Visa min plats';
    div.onclick = function(){
      if (navigator.geolocation){
        navigator.geolocation.getCurrentPosition(
          function(pos){
            const lat = pos.coords.latitude;
            const lon = pos.coords.longitude;
            const userMarker = L.marker([lat, lon], {
              icon: L.icon({
                iconUrl: 'https://cdn-icons-png.flaticon.com/512/64/64113.png',
                iconSize: [24, 24]
              })
            }).addTo(map);
            userMarker.bindPopup('📍 Du är här!<br><b>Lat:</b> '+lat.toFixed(5)+'<br><b>Lon:</b> '+lon.toFixed(5)).openPopup();
            map.setView([lat, lon], 14);
          },
          function(err){
            alert('Kunde inte hämta position: ' + err.message);
          }
        );
      } else {
        alert('Geolocation stöds inte av din webbläsare.');
      }
    };
    return div;
  };
  btn.addTo(map);
}
addLocateButton(window.map);
</script>
"""
m.get_root().html.add_child(folium.Element(geolocate_js))

# --------------------------------------------------
# 🎛️ 5. Layer-kontroll + spara
# --------------------------------------------------
folium.LayerControl(collapsed=False).add_to(m)
m.save("hundparker_folium_snygg.html")
m.save("hundparker_folium_snygg_3_3.html")
print("✅ Klar: hundparker_folium_snygg_3_3.html (Hundlistan + OSM-lager)")


In [ ]:
m


In [ ]:
import folium
import json
import requests
import os

# --------------------------------------------------
# 🗺️ 1. Skapa grundkartan
# --------------------------------------------------
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# --------------------------------------------------
# 🐾 2. Infobox (öppen från start, collapsible)
# --------------------------------------------------
from datetime import datetime
created = datetime.now().strftime("%Y-%m-%d kl. %H:%M")

info_html = f"""
<style>
#infoBox {{
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 260px;
  transition: all 0.3s ease-in-out;
}}
#toggleBtn {{
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}}
#toggleBtn:hover {{ background-color: #005fa3; }}
#infoContent {{ display: block; margin-top: 8px; }}
.version-list {{
  text-align: left;
  margin-top: 10px;
  padding-left: 12px;
}}
.version-list a {{
  color: #0077cc;
  text-decoration: none;
}}
.version-list a:hover {{
  text-decoration: underline;
}}
.version-list li {{
  margin-bottom: 4px;
}}
@media (max-width: 600px) {{
  #infoBox {{ max-width: 190px; font-size: 12px; }}
}}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <b style="display:block; text-align:center;">📌 Versioner</b>
    <ol class="version-list">
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OpenStreetMap-lager</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_2.html" target="_blank">🌍 Hundlistan + OSM-version</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_4.html" target="_blank">📍 Min plats bottomright</a></li>
    </ol>

    <div style="text-align:center; margin-top:8px;">
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank"
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a><br>
      <span style="color:#555; font-size:11px;">🕒 Skapad {created}</span>
    </div>
  </div>
</div>

<script>
  const btn = document.getElementById('toggleBtn');
  const content = document.getElementById('infoContent');
  let open = true;
  btn.onclick = () => {{
    open = !open;
    content.style.display = open ? 'block' : 'none';
    btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
  }};
</script>
"""


m.get_root().html.add_child(folium.Element(info_html))

# --------------------------------------------------
# 🦴 3. Hundlistan-data (lager 1)
# --------------------------------------------------
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

hundlistan_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")

for feature in data["features"]:
    props = feature["properties"]
    lon, lat = feature["geometry"]["coordinates"]

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress','Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan','Okänt län')}</span><br>
      <span style="color:#777;">🧭 
        <span id='coord_{lat:.5f}_{lon:.5f}'>{lat:.5f}, {lon:.5f}</span>
        <button onclick="navigator.clipboard.writeText('{lat:.5f}, {lon:.5f}'); 
                         this.innerText='✅'; 
                         setTimeout(()=>this.innerText='📋',1000);"
                style="background:none; border:none; cursor:pointer; color:#0077cc; font-size:13px;"
                title="Kopiera koordinat">📋</button>
      </span><br><br>
    
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a><br>
      <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
         target="_blank" style="color:#d97706; text-decoration:none;">
         🗺️ Skapa OSM Note här
      </a><br>
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank" 
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a>
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hundlistan_layer)

hundlistan_layer.add_to(m)

# --------------------------------------------------
# 🐕‍🦺 4. OSM Hundrastgårdar (lager 2)
# --------------------------------------------------
osm_file = "osm_dogparks_sweden.json"

if os.path.exists(osm_file):
    print("📂 Läser OSM-data lokalt...")
    with open(osm_file, "r", encoding="utf-8") as f:
        osm_data = json.load(f)
else:
    print("⏳ Hämtar hundrastgårdar från OSM...")
    overpass_url = "https://overpass-api.de/api/interpreter"
    sweden_bbox = "55.0,10.5,69.2,24.2"
    query = f"""
    [out:json][timeout:60];
    nwr["leisure"="dog_park"]({sweden_bbox});
    out center;
    """
    r = requests.get(overpass_url, params={"data": query})
    osm_data = r.json()
    with open(osm_file, "w", encoding="utf-8") as f:
        json.dump(osm_data, f, ensure_ascii=False, indent=2)
    print(f"✅ Sparade {len(osm_data['elements'])} objekt till {osm_file}")

osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for el in osm_data["elements"]:
    if "lat" in el and "lon" in el:
        lat, lon = el["lat"], el["lon"]
    elif "center" in el:
        lat, lon = el["center"]["lat"], el["center"]["lon"]
    else:
        continue

    name = el["tags"].get("name", "Okänd rastgård")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:purple;">🐕 {name}</b><br>
      <span style="color:#777;">🧭 <span id='coord_{lat:.5f}_{lon:.5f}'>{lat:.5f}, {lon:.5f}</span>
        <button onclick="navigator.clipboard.writeText('{lat:.5f}, {lon:.5f}'); 
                         this.innerText='✅'; 
                         setTimeout(()=>this.innerText='📋',1000);"
                style="background:none; border:none; cursor:pointer; color:#0077cc; font-size:13px;"
                title="Kopiera koordinat">📋</button>
      </span><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {el['id']}<br>
          <a href="https://www.openstreetmap.org/{el['type']}/{el['id']}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a><br>
          <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
             target="_blank" style="color:#d97706;">🗺️ Skapa OSM Note här</a>
        </p>
      </details>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)

osm_layer.add_to(m)
# --------------------------------------------------
# 📍 6. "Min plats"-knapp (geolocation) — förbättrad version
# --------------------------------------------------
geolocate_js = """
<script>
function addLocateButton(map){
  const btn = L.control({position: 'bottomright'});
  btn.onAdd = function(){
    const div = L.DomUtil.create('div', 'leaflet-bar leaflet-control leaflet-control-custom');
    div.innerHTML = '📍<br><small style="font-size:10px;">Min plats</small>';
    div.style.backgroundColor = 'white';
    div.style.cursor = 'pointer';
    div.style.textAlign = 'center';
    div.style.padding = '4px';
    div.title = 'Visa min plats';
    div.onclick = function(){
      if (navigator.geolocation){
        navigator.geolocation.getCurrentPosition(
          function(pos){
            const lat = pos.coords.latitude;
            const lon = pos.coords.longitude;
            const userMarker = L.marker([lat, lon], {
              icon: L.icon({
                iconUrl: 'https://cdn-icons-png.flaticon.com/512/64/64113.png',
                iconSize: [24, 24]
              })
            }).addTo(map);
            userMarker.bindPopup('📍 Du är här!<br><b>Lat:</b> '+lat.toFixed(5)+'<br><b>Lon:</b> '+lon.toFixed(5)).openPopup();
            map.setView([lat, lon], 14);
          },
          function(err){
            alert('Kunde inte hämta position: ' + err.message);
          }
        );
      } else {
        alert('Geolocation stöds inte av din webbläsare.');
      }
    };
    return div;
  };
  btn.addTo(map);
}

// Vänta tills Folium-kartan är laddad
setTimeout(function() {
  // Sök efter Folium-kartans variabel (den heter typ "map_123abc456def")
  for (const key in window) {
    if (key.startsWith("map_")) {
      addLocateButton(window[key]);
      break;
    }
  }
}, 500);
</script>
"""
m.get_root().html.add_child(folium.Element(geolocate_js))

# --------------------------------------------------
# 🎛️ 5. Layer-kontroll + spara
# --------------------------------------------------
folium.LayerControl(collapsed=False).add_to(m)
m.save("hundparker_folium_snygg.html")
m.save("hundparker_folium_snygg_3_4_2.html")
print("✅ Klar: hundparker_folium_snygg_3_4_2.html (Min plats-version)")


In [ ]:
m

